In [ ]:
import datetime
import pandas.tseries.offsets as off
import globeop_reports as go
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

from utils.db import dbengine
from yieldcurve import YC
from quantlib.termstructures.yield_term_structure import YieldTermStructure

engine  = dbengine('dawndb')
Sengine = dbengine('serenitasdb')

In [ ]:
#Plot this month's PNL
pnl_alloc_last_month = pnl_alloc.xs(report_date)
ax = pnl_alloc_last_month['strat_return'].plot(kind='bar', figsize = (6,6), width = .35)
ax.set_xlabel('Strategy')
ax.set_ylabel('Return (%)')
x_ticks = ax.get_xticks()
y_ticks = ax.get_yticks()
ax.set_yticklabels(['{:.2f}%'.format(y*100) for y in y_ticks])
plt.tight_layout()

In [ ]:
#Pnl through time
#pnl_alloc_sum = pnl_alloc['mtdtotalbookpl']/ pnl_alloc['mtdtotalbookpl'].groupby(['date']).sum()
#pnl_alloc_sum['strat_return'].unstack().plot(kind='bar')

In [ ]:
#Capital Allocation - Find the strategies that are not defined: undefined needs to be mapped in strat_map
port = go.get_portfolio().reset_index()
cap_alloc = port.reset_index().merge(strats, on=['strat', 'custacctname'], how='left')
undefined = cap_alloc[cap_alloc.pnl.isna()].groupby(['strat', 'custacctname']).last()
alloc1 = cap_alloc[cap_alloc.periodenddate == report_date].groupby(['capital']).sum()

In [ ]:
# create piechart and add a circle at the center
alloc1['percentage'] = alloc1['endbooknav']/alloc1['endbooknav'].sum()
ax = alloc1[alloc1>0]['percentage'].plot(kind='pie', figsize=(8,4), autopct='%1.1f%%', pctdistance=1.25, labeldistance=1.5)
ax.add_artist(plt.Circle((0,0), 0.7, color='white'))
ax.axis('equal')
plt.tight_layout()

In [ ]:
#Number of bond positions by strategy by month
df = go.get_portfolio()
df = df[(df.custacctname == 'V0NSCLMAMB') &
        ~(df.invid.isin(['USD', 'CAD', 'EUR'])) & (df.endqty > 0)]
df = df.groupby(pd.Grouper(freq='M'), group_keys=False).apply(lambda df: df.loc[df.index[-1]])
num_bond_pos = df.groupby(['periodenddate', 'port']).identifier.nunique().unstack()

In [ ]:
#Number of bond trades by direction by month
sql_string = "SELECT * FROM bonds"
df = pd.read_sql_query(sql_string, dbengine('dawndb'), parse_dates=['trade_date'],
                           index_col=['trade_date'])
df = df.groupby([pd.Grouper(freq='M'), 'buysell'], group_keys=False).identifier.count().unstack()
idx = pd.date_range(df.index[0], df.index[-1], freq = 'M')
num_bond_trades = df.reindex(idx, fill_value = 0)

In [ ]:
#capital allocation across time
cap_alloc_time = cap_alloc.groupby(['periodenddate','capital']).sum()
cap_alloc_time = cap_alloc_time.reset_index('capital').groupby(pd.Grouper(freq='M'), group_keys=False).apply(lambda df: df.loc[df.index[-1]])
cap_alloc_time['perc'] = cap_alloc_time['endbooknav'].groupby('periodenddate').apply(lambda x: x/x.sum())
cap_alloc_time = cap_alloc_time.set_index('capital', append=True)['perc'].unstack()

In [ ]:
ax = cap_alloc_time.plot.bar(stacked=True, legend=False, figsize=(10,6))

#Format Y Axis
vals = ax.get_yticks()
ax.set_yticklabels(['{:3.0f}%'.format(x*100) for x in vals])

#Format X Axis
visible = ax.xaxis.get_ticklabels()[::6]
for label in ax.xaxis.get_ticklabels():
    if label not in visible:
        label.set_visible(False)
ax.xaxis.set_major_formatter(plt.FixedFormatter(df.index.to_series().dt.strftime("%b %Y")))
ax.xaxis.set_label_text("")
lgd = ax.legend(loc='lower center', bbox_to_anchor=(0.50, -0.6), ncol=4)
plt.tight_layout()
ax.figure.savefig("/home/serenitas/edwin/PythonGraphs/cap_alloc_1.png", bbox_extra_artists=(lgd,), bbox_inches='tight')

In [ ]:
#Calculate Interests allocation 
sql_string = "select periodenddate, strat, sum(endqty) as bal, counterparty " \
             "from valuation_reports where invid = 'USDLOAN' and " \
             "extract(month from periodenddate) = %s and " \
             "extract(year from periodenddate) = %s " \
             "group by periodenddate, strat, counterparty " \
             "order by periodenddate desc"
df = pd.read_sql_query(sql_string, dbengine('dawndb'), 
                       parse_dates=['periodenddate'],
                       index_col=['strat', 'counterparty'],
                       params=[report_date.month, report_date.year])
df['day_frac'] = -(df.groupby(level=['strat','counterparty'])['periodenddate'].transform(lambda s:
                                                s.diff().astype('timedelta64[D]') / 360)).astype(float)
df = df.fillna(0)
r = {}
yc = YieldTermStructure()
for t in df['periodenddate'].unique():
    yc.link_to(YC(evaluation_date=pd.Timestamp(t)))
    r[pd.Timestamp(t)] = (float(yc.zero_rate(.083333)))
rates = pd.DataFrame.from_dict(r, orient='index')
df = df.reset_index().set_index('periodenddate', drop=False).join(rates)
df = df.rename(columns={0: 'rate'})
df = df.set_index(['strat','counterparty'], append=True)
df['interest'] = df['rate'] * df['day_frac'] * df['bal']
interests = df['interest'].groupby(level=['counterparty','strat']).sum()